In [1]:
# Use the trained astroBERT model to make SciX category predictions

# Tutorial 3 - Using astroBERT to make SciX category predictions
This tutorial shows you how to use a finetuned astroBERT to classify paper abstracts into SciX Categories. 

In [2]:
# 1 - load the model

In [3]:
from transformers import AutoModelForSequenceClassification

In [4]:
pretrained_model_name_or_path = 'adsabs/astroBERT'
revision = 'SciX-Categorizer'

In [5]:
# load model
model = AutoModelForSequenceClassification.from_pretrained(pretrained_model_name_or_path=pretrained_model_name_or_path,
                                                           revision=revision
                                                          )

In [6]:
# check out the categories
model.config.id2label

{0: 'Astronomy',
 1: 'Heliophysics',
 2: 'Planetary Science',
 3: 'Earth Science',
 4: 'NASA-funded Biophysics',
 5: 'Other Physics',
 6: 'Other',
 7: 'Text Garbage'}

In [7]:
# load some texts and tokenize them
paper_abstracts = ['Star Formation Efficiencies and Lifetimes of Giant Molecular Clouds in the Milky Way. We use a sample of the 13 most luminous WMAP Galactic free-free sources, responsible for 33% of the free-free emission of the Milky Way, to investigate star formation. The sample contains 40 star-forming complexes; we combine this sample with giant molecular cloud (GMC) catalogs in the literature to identify the host GMCs of 32 of the complexes. We estimate the star formation efficiency epsilonGMC and star formation rate per free-fall time epsilonff. We find that epsilonGMC ranges from 0.002 to 0.2, with an ionizing luminosity-weighted average langepsilonGMCrang Q = 0.08, compared to the Galactic average ≈0.005. Turning to the star formation rate per free-fall time, we find values that range up to ɛ_ff ≡ τ _ff \cdot \dot{M}_*/M_GMC≈ 1. Weighting by ionizing luminosity, we find an average of langepsilonffrang Q = 0.14-0.24 depending on the estimate of the age of the system. Once again, this is much larger than the Galaxy-wide average value epsilonff = 0.006. We show that the lifetimes of GMCs at the mean mass found in our sample is 27 ± 12 Myr, a bit less than three free-fall times. The GMCs hosting the most luminous clusters are being disrupted by those clusters. Accordingly, we interpret the range in epsilonff as the result of a time-variable star formation rate; the rate of star formation increases with the age of the host molecular cloud, until the stars disrupt the cloud. These results are inconsistent with the notion that the star formation rate in Milky Way GMCs is determined by the properties of supersonic turbulence.',
                   'Random Forests. Random forests are a combination of tree predictors such that each tree depends on the values of a random vector sampled independently and with the same distribution for all trees in the forest. The generalization error for forests converges a.s. to a limit as the number of trees in the forest becomes large. The generalization error of a forest of tree classifiers depends on the strength of the individual trees in the forest and the correlation between them. Using a random selection of features to split each node yields error rates that compare favorably to Adaboost (Y. Freund & R. Schapire, Machine Learning: Proceedings of the Thirteenth International conference, ***, 148-156), but are more robust with respect to noise. Internal estimates monitor error, strength, and correlation and these are used to show the response to increasing the number of features used in the splitting. Internal estimates are also used to measure variable importance. These ideas are also applicable to regression.',
                   'Galactic Stellar and Substellar Initial Mass Function,  We review recent determinations of the present-day mass function (PDMF) and initial mass function (IMF) in various components of the Galaxy-disk, spheroid, young, and globular clusters-and in conditions characteristic of early star formation. As a general feature, the IMF is found to depend weakly on the environment and to be well described by a power-law form for m>~1 Msolar and a lognormal form below, except possibly for early star formation conditions. The disk IMF for single objects has a characteristic mass around mc~0.08 Msolar and a variance in logarithmic mass σ~0.7, whereas the IMF for multiple systems has mc~0.2 Msolar and σ~0.6. The extension of the single MF into the brown dwarf regime is in good agreement with present estimates of L- and T-dwarf densities and yields a disk brown dwarf number density comparable to the stellar one, nBD~n*~0.1 pc-3. The IMF of young clusters is found to be consistent with the disk field IMF, providing the same correction for unresolved binaries, confirming the fact that young star clusters and disk field stars represent the same stellar population. Dynamical effects, yielding depletion of the lowest mass objects, are found to become consequential for ages >~130 Myr. The spheroid IMF relies on much less robust grounds. The large metallicity spread in the local subdwarf photometric sample, in particular, remains puzzling. Recent observations suggest that there is a continuous kinematic shear between the thick-disk population, present in local samples, and the genuine spheroid one. This enables us to derive only an upper limit for the spheroid mass density and IMF. Within all the uncertainties, the latter is found to be similar to the one derived for globular clusters and is well represented also by a lognormal form with a characteristic mass slightly larger than for the disk, mc~0.2-0.3 Msolar, excluding a significant population of brown dwarfs in globular clusters and in the spheroid. The IMF characteristic of early star formation at large redshift remains undetermined, but different observational constraints suggest that it does not extend below ~1 Msolar. These results suggest a characteristic mass for star formation that decreases with time, from conditions prevailing at large redshift to conditions characteristic of the spheroid (or thick disk) to present-day conditions. These conclusions, however, remain speculative, given the large uncertainties in the spheroid and early star IMF determinations. These IMFs allow a reasonably robust determination of the Galactic present-day and initial stellar and brown dwarf contents. They also have important galactic implications beyond the Milky Way in yielding more accurate mass-to-light ratio determinations. The mass-to-light ratios obtained with the disk and the spheroid IMF yield values 1.8-1.4 times smaller than for a Salpeter IMF, respectively, in agreement with various recent dynamical determinations. This general IMF determination is examined in the context of star formation theory. None of the theories based on a Jeans-type mechanism, where fragmentation is due only to gravity, can fulfill all the observational constraints on star formation and predict a large number of substellar objects. On the other hand, recent numerical simulations of compressible turbulence, in particular in super-Alfvénic conditions, seem to reproduce both qualitatively and quantitatively the stellar and substellar IMF and thus provide an appealing theoretical foundation. In this picture, star formation is induced by the dissipation of large-scale turbulence to smaller scales through radiative MHD shocks, producing filamentary structures. These shocks produce local nonequilibrium structures with large density contrasts, which collapse eventually in gravitationally bound objects under the combined influence of turbulence and gravity. The concept of a single Jeans mass is replaced by a distribution of local Jeans masses, representative of the lognormal probability density function of the turbulent gas. Objects below the mean thermal Jeans mass still have a possibility to collapse, although with a decreasing probability. The page charges for this Review were partially covered by a generous gift from a PASP supporter.',
                  ]


In [8]:
from transformers import AutoTokenizer

In [9]:
tokenizer = AutoTokenizer.from_pretrained(pretrained_model_name_or_path=pretrained_model_name_or_path,
                                          revision=revision,
                                          do_lower_case=False)

In [10]:
list_of_texts_tokenized_input_ids = tokenizer(paper_abstracts, max_length=512, truncation=True, pad_to_max_length=True, add_special_tokens=True)['input_ids']


/proj.adsnlp/jupyter-lab/one/ads/.local/lib/python3.8/site-packages/transformers/tokenization_utils_base.py:2271: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


In [11]:
from torch import no_grad, tensor

In [12]:
# forward call
with no_grad():
        predictions = model(input_ids=tensor(list_of_texts_tokenized_input_ids)).logits.sigmoid().tolist()


In [13]:
print(predictions)

[[0.9995561242103577, 0.00014585199824068695, 0.00038051357842050493, 0.0002408829896012321, 8.467026191283367e-07, 0.00015598340542055666, 9.46967484196648e-05, 6.663293333986076e-06], [7.198489038273692e-05, 3.548982203938067e-05, 0.005394219420850277, 0.9924236536026001, 4.508056463237153e-06, 0.0031560249626636505, 0.005173855926841497, 2.667580520210322e-05], [0.9982689619064331, 0.0003360261907801032, 0.003926889039576054, 0.00021573311823885888, 5.955367328169814e-07, 0.0001352201506961137, 2.13952280319063e-05, 4.8363999667344615e-06]]


In [14]:
import numpy as np

In [15]:
# check out the max prediction score
for i, scores in enumerate(predictions):
    print('For abstract {}, the model predicts {} with score {:.4f}'.format(i, model.config.id2label[np.argmax(scores)], np.max(scores)))

For abstract 0, the model predicts Astronomy with score 0.9996
For abstract 1, the model predicts Earth Science with score 0.9924
For abstract 2, the model predicts Astronomy with score 0.9983
